<a href="https://colab.research.google.com/github/Sagargomad/My_projects/blob/main/generate_fake_english_text_using_RNN.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
import random
import numpy as np
import tensorflow as tf
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import LSTM,Dense,Activation,Dropout,BatchNormalization
from tensorflow.keras.optimizers import RMSprop,Adam
from tensorflow.keras.callbacks import ModelCheckpoint, EarlyStopping,ReduceLROnPlateau

In [ ]:
filepath = tf.keras.utils.get_file('shakespear.txt','https://cs.stanford.edu/people/karpathy/char-rnn/shakespeare_input.txt')

4573338/4573338 [==============================] - 1s 0us/step


In [ ]:
filepath

'/root/.keras/datasets/shakespear.txt'

In [ ]:
text=open(filepath,'r')

In [ ]:
text.read()

"First Citizen:\nBefore we proceed any further, hear me speak.\n\nAll:\nSpeak, speak.\n\nFirst Citizen:\nYou are all resolved rather to die than to famish?\n\nAll:\nResolved. resolved.\n\nFirst Citizen:\nFirst, you know Caius Marcius is chief enemy to the people.\n\nAll:\nWe know't, we know't.\n\nFirst Citizen:\nLet us kill him, and we'll have corn at our own price.\nIs't a verdict?\n\nAll:\nNo more talking on't; let it be done: away, away!\n\nSecond Citizen:\nOne word, good citizens.\n\nFirst Citizen:\nWe are accounted poor citizens, the patricians good.\nWhat authority surfeits on would relieve us: if they\nwould yield us but the superfluity, while it were\nwholesome, we might guess they relieved us humanely;\nbut they think we are too dear: the leanness that\nafflicts us, the object of our misery, is as an\ninventory to particularise their abundance; our\nsufferance is a gain to them Let us revenge this with\nour pikes, ere we become rakes: for the gods know I\nspeak this in hunger 

In [ ]:
text=open(filepath,'r').read().lower()

In [ ]:
text

"first citizen:\nbefore we proceed any further, hear me speak.\n\nall:\nspeak, speak.\n\nfirst citizen:\nyou are all resolved rather to die than to famish?\n\nall:\nresolved. resolved.\n\nfirst citizen:\nfirst, you know caius marcius is chief enemy to the people.\n\nall:\nwe know't, we know't.\n\nfirst citizen:\nlet us kill him, and we'll have corn at our own price.\nis't a verdict?\n\nall:\nno more talking on't; let it be done: away, away!\n\nsecond citizen:\none word, good citizens.\n\nfirst citizen:\nwe are accounted poor citizens, the patricians good.\nwhat authority surfeits on would relieve us: if they\nwould yield us but the superfluity, while it were\nwholesome, we might guess they relieved us humanely;\nbut they think we are too dear: the leanness that\nafflicts us, the object of our misery, is as an\ninventory to particularise their abundance; our\nsufferance is a gain to them let us revenge this with\nour pikes, ere we become rakes: for the gods know i\nspeak this in hunger 

In [ ]:
characters=sorted(set(text))

In [ ]:
#These are all the unique text which have appeared in our texts
characters

['\n',
 ' ',
 '!',
 '$',
 '&',
 "'",
 ',',
 '-',
 '.',
 '3',
 ':',
 ';',
 '?',
 '[',
 ']',
 'a',
 'b',
 'c',
 'd',
 'e',
 'f',
 'g',
 'h',
 'i',
 'j',
 'k',
 'l',
 'm',
 'n',
 'o',
 'p',
 'q',
 'r',
 's',
 't',
 'u',
 'v',
 'w',
 'x',
 'y',
 'z']

In [ ]:
len(characters)

41

In [ ]:
char_to_index=dict((c,i) for i,c in enumerate(characters))

In [ ]:
char_to_index

{'\n': 0,
 ' ': 1,
 '!': 2,
 '$': 3,
 '&': 4,
 "'": 5,
 ',': 6,
 '-': 7,
 '.': 8,
 '3': 9,
 ':': 10,
 ';': 11,
 '?': 12,
 '[': 13,
 ']': 14,
 'a': 15,
 'b': 16,
 'c': 17,
 'd': 18,
 'e': 19,
 'f': 20,
 'g': 21,
 'h': 22,
 'i': 23,
 'j': 24,
 'k': 25,
 'l': 26,
 'm': 27,
 'n': 28,
 'o': 29,
 'p': 30,
 'q': 31,
 'r': 32,
 's': 33,
 't': 34,
 'u': 35,
 'v': 36,
 'w': 37,
 'x': 38,
 'y': 39,
 'z': 40}

In [ ]:
index_to_char=dict((i,c) for i,c in enumerate(characters))

In [ ]:
index_to_char

{0: '\n',
 1: ' ',
 2: '!',
 3: '$',
 4: '&',
 5: "'",
 6: ',',
 7: '-',
 8: '.',
 9: '3',
 10: ':',
 11: ';',
 12: '?',
 13: '[',
 14: ']',
 15: 'a',
 16: 'b',
 17: 'c',
 18: 'd',
 19: 'e',
 20: 'f',
 21: 'g',
 22: 'h',
 23: 'i',
 24: 'j',
 25: 'k',
 26: 'l',
 27: 'm',
 28: 'n',
 29: 'o',
 30: 'p',
 31: 'q',
 32: 'r',
 33: 's',
 34: 't',
 35: 'u',
 36: 'v',
 37: 'w',
 38: 'x',
 39: 'y',
 40: 'z'}

In [ ]:
SEQ_LENGTH=40
STEP_SIZE=3

In [ ]:
sentences=[]
next_characters=[]

In [ ]:
len(text)

4573338

In [ ]:
for i in range(0,len(text)-SEQ_LENGTH,STEP_SIZE):
    sentences.append(text[i:i+SEQ_LENGTH])
    next_characters.append(text[i+SEQ_LENGTH])

In [ ]:
next_characters[:10]

['t', 'r', 'h', 'r', 'e', 'p', 'k', '\n', 'l', 's']

In [ ]:
print(len(sentences))
print(SEQ_LENGTH)

1524433
40


In [ ]:
x=np.zeros((len(sentences),SEQ_LENGTH,len(characters)),dtype=bool)

In [ ]:
len(x[0])

40

In [ ]:
y=np.zeros((len(next_characters),len(characters)),dtype=bool)

In [ ]:
#Here we are doing one-hot encoding
for i,sentence in enumerate(sentences):
    for t,character in enumerate(sentence):
        x[i,t,char_to_index[character]]=1
    y[i,char_to_index[next_characters[i]]]=1

In [ ]:
#Number of epochs
num_epochs=8

In [ ]:
def xy_generator(x,y):
    p=0
    for s in range(len(x)//16):
        z=(x[p:(p+16)],y[p:(p+16)])
        p+=16
        yield z
train_generator=xy_generator(x,y)

In [ ]:
print(len(x))
#Steps_per_epoch
steps_epoch=len(list(train_generator))
print(steps_epoch)

1524433
95277


In [ ]:
def xy_generator(x,y):
    for epoch in range(num_epochs):
        p=0
        for s in range(len(x)//16):
            z=(x[p:(p+16)],y[p:(p+16)])
            p+=16
            yield z
train_generator=xy_generator(x,y)

In [ ]:
# Set the print options to display the entire array
np.set_printoptions(threshold=np.inf)

In [ ]:
next_characters[0]

't'

In [ ]:
model=Sequential()

In [ ]:
model.add(LSTM(256,input_shape=(SEQ_LENGTH,len(characters))))

In [ ]:
model.add(BatchNormalization())

In [ ]:
model.add(Dense(len(characters),activation='softmax'))

In [ ]:
#model.compile(loss='categorical_crossentropy',optimizer=RMSprop(learning_rate=0.001),metrics=['accuracy'])
model.compile(loss='categorical_crossentropy',optimizer="adam",metrics=['accuracy'])

In [ ]:
es = EarlyStopping(monitor='accuracy',patience=5,restore_best_weights=True)
lrr = ReduceLROnPlateau(monitor='accuracy', patience=2, verbose=1, factor=0.3, min_lr=0.000001,mode='max')

In [ ]:
model.fit(train_generator,batch_size=16,callbacks=[es,lrr],epochs=num_epochs,steps_per_epoch=steps_epoch)

Epoch 1/8
95277/95277 [==============================] - 631s 7ms/step - loss: 1.2000 - accuracy: 0.6467 - lr: 0.0010
Epoch 2/8
95277/95277 [==============================] - 622s 7ms/step - loss: 0.6760 - accuracy: 0.8077 - lr: 0.0010
Epoch 3/8
95277/95277 [==============================] - 612s 6ms/step - loss: 0.5689 - accuracy: 0.8397 - lr: 0.0010
Epoch 4/8
95277/95277 [==============================] - 612s 6ms/step - loss: 0.5138 - accuracy: 0.8558 - lr: 0.0010
Epoch 5/8
95277/95277 [==============================] - 606s 6ms/step - loss: 0.4786 - accuracy: 0.8663 - lr: 0.0010
Epoch 6/8
95277/95277 [==============================] - 612s 6ms/step - loss: 0.4990 - accuracy: 0.8623 - lr: 0.0010
Epoch 7/8
95277/95277 [==============================] - 611s 6ms/step - loss: 0.4377 - accuracy: 0.8785 - lr: 0.0010
Epoch 8/8
95277/95277 [==============================] - 611s 6ms/step - loss: 0.5060 - accuracy: 0.8597 - lr: 0.0010


In [ ]:
model.save('text_generator_1.model')

In [ ]:
model=tf.keras.models.load_model('text_generator_1.model')

In [ ]:
"""start_index = random.randint(0, len(text) - SEQ_LENGTH)
generated = ''
sentence = text[start_index: start_index + SEQ_LENGTH]
generated += sentence
x_predictions = np.zeros((1, SEQ_LENGTH, len(characters)))
for t, char in enumerate(sentence):
            x_predictions[0, t, char_to_index[char]] = 1"""

In [ ]:
#prediction=model.predict(x_predictions, verbose=1)

1/1 [==============================] - 0s 15ms/step


In [ ]:
#prediction

array([[5.5228080e-05, 1.4317597e-03, 9.9862982e-06, 1.7237825e-08,
        1.8481359e-08, 1.3650335e-04, 4.8655039e-04, 4.0973468e-05,
        1.6598506e-05, 2.2262007e-08, 4.6982382e-06, 2.9530720e-05,
        1.3744485e-05, 1.9566052e-08, 2.4191836e-08, 6.9048372e-04,
        6.0698427e-03, 1.4302658e-04, 1.3052025e-04, 1.1731693e-02,
        2.7103075e-03, 6.8656431e-04, 1.3202503e-04, 1.0950595e-02,
        7.5233635e-05, 1.3373629e-04, 9.4015151e-01, 3.4888217e-04,
        2.8918736e-08, 7.5061349e-03, 2.9802279e-04, 4.2774759e-06,
        1.8164743e-05, 8.2456218e-03, 3.9233471e-04, 6.2946682e-03,
        2.5254676e-05, 7.8761208e-05, 2.0829992e-05, 9.3249575e-04,
        3.2915177e-06]], dtype=float32)

In [ ]:
#predicted_class = np.argmax(prediction, axis=1)

In [ ]:
#predicted_class

array([26], dtype=int64)

In [ ]:
#a=predicted_class[0]

In [ ]:
#generated+=index_to_char[a]

In [ ]:
#generated

'modern friends withal; and say,\nsome nobl'

In [ ]:
def generate_text(length):
    start_index = random.randint(0, len(text) - SEQ_LENGTH)
    generated = ''
    sentence = text[start_index: start_index + SEQ_LENGTH]
    generated += sentence
    for i in range(length):
        x_predictions = np.zeros((1, SEQ_LENGTH, len(characters)))
        for t, char in enumerate(sentence):
            x_predictions[0, t, char_to_index[char]] = 1

        predictions = model.predict(x_predictions, verbose=0)
        predicted_class = np.argmax(predictions, axis=1)[0]
        next_character = index_to_char[predicted_class]
        generated += next_character
        sentence = sentence[1:] + next_character
    return generated

In [ ]:
print(generate_text(100))

 patience; but am bolden'd
under your pray at at expectent sats there
so cannant willing to my upon his salsa,
except sals teater thrand him


In [ ]:
len(generate_text(100))

140